In [ ]:
!pip install shapely

### Intro to Geojson file

In this notebook

    1. We load a geojson file containing Mc Donalds locations.
    
    2. Read the file into a geopandas dataframe
    
    3. Use the dataframe to plot the locations in folium
    

In [1]:
#set the enviroment not to use pygeos for geopandas, to avoid the warning about migrating from pygeos to shapely!
import os
os.environ['USE_PYGEOS'] = '0'

# Load libraries
import pandas as pd
import geopandas as gpd
from shapely.geometry import Point, LineString, Polygon
import networkx as nx
import osmnx as ox
import matplotlib.pyplot as plt
from descartes import PolygonPatch
from IPython.display import IFrame
#ox.config(log_console=True, use_cache=True)

import numpy as np
from shapely.wkt import loads

import folium
import matplotlib.pyplot as plt
plt.rcParams["figure.dpi"] = 200

In [2]:
#Loading the geojson file containing the polygons
poly_df= gpd.read_file('gaps.geojson')
poly_df.head()

geometry
0  LINESTRING (18.39823 -33.90590, 18.39791 -33.9...
1  LINESTRING (18.42106 -33.91660, 18.41897 -33.9...
2  LINESTRING (18.50871 -33.92441, 18.49935 -33.9...
3  LINESTRING (18.44231 -33.92628, 18.46121 -33.9...
4  LINESTRING (18.42661 -33.99979, 18.42186 -34.0...

In [3]:
#Load the locations file
df= pd.read_csv('geo_locations_file.csv')
df.head()

Store       latt       long
0  Howard Centre, Forest Dr Service Rd, Pinelands... -33.935825  18.506401
1  Cape Town City Centre Cnr Strand Street &, 24A... -33.920610  18.421170
2      199 Voortrekker Rd, Maitland, Cape Town, 7405 -33.922920  18.485990
3  Cnr Koeberg &, Bosmansdam Rd, Milnerton, Cape ... -33.877860  18.499540
4   Kloof St, Gardens, Cape Town, 800,  021 422 1371 -33.931932  18.408858

In [4]:
m = folium.Map(location = [-33.9152209,18.3758852], zoom_start = 10,tiles="Stamen Terrain", control_scale=True)
m

In [5]:

for index, store in df.iterrows():
    folium.Marker([store["latt"], 
                   store["long"]], 
                  popup = store["Store"]).add_to(m)

m

In [6]:

#instatiating the map with South Africa as the centre
folium.GeoJson(poly_df.to_json(), style_function=lambda x:{'fillColor': 'red'}).add_to(m)
m

In [7]:
#LineStrings dataframe
poly_df_1 = poly_df[poly_df.geometry.type == 'LineString']
#df_1 = df.iloc[:21,:]

In [8]:
poly_df_1.head()

geometry
0  LINESTRING (18.39823 -33.90590, 18.39791 -33.9...
1  LINESTRING (18.42106 -33.91660, 18.41897 -33.9...
2  LINESTRING (18.50871 -33.92441, 18.49935 -33.9...
3  LINESTRING (18.44231 -33.92628, 18.46121 -33.9...
4  LINESTRING (18.42661 -33.99979, 18.42186 -34.0...

In [9]:
#LineStrings Map
m_1 = folium.Map([-27.9150338,24.8737837], zoom_start=6,tiles="Stamen Terrain")
folium.GeoJson(poly_df_1.to_json()).add_to(m_1)
m_1

In [10]:
#Polygons dataframe
poly_df_2 = poly_df[poly_df.geometry.type == 'Polygon']
poly_df_2.head()

geometry
21  POLYGON ((28.98896 -25.97438, 28.98896 -27.097...
22  POLYGON ((26.16460 -29.06068, 26.16238 -29.060...
23  POLYGON ((26.17981 -29.12544, 26.17612 -29.125...
24  POLYGON ((26.24715 -29.05952, 26.24298 -29.059...
25  POLYGON ((28.10305 -25.68582, 28.09703 -25.686...

In [11]:
#Polygons map
m_2 = folium.Map([-27.9150338,24.8737837], zoom_start=5,tiles="Stamen Terrain")
folium.GeoJson(poly_df_2.to_json()).add_to(m_2)
m_2

In [12]:
#!pip install osmnx
#!pip install networkx

### Calculating travel time for the locations
Here I got inspiration from the following links:

https://towardsdatascience.com/how-to-calculate-travel-time-for-any-location-in-the-world-56ce639511f


https://gis.stackexchange.com/questions/294206/how-to-create-a-simple-polygon-from-coordinates-in-geopandas-with-python



In [13]:
df_geo = gpd.GeoDataFrame(df, geometry = gpd.points_from_xy(df.long, df.latt))
df_geo.dtypes

Store         object
latt         float64
long         float64
geometry    geometry
dtype: object

In [14]:
df_geo.head()

Store       latt       long  \
0  Howard Centre, Forest Dr Service Rd, Pinelands... -33.935825  18.506401   
1  Cape Town City Centre Cnr Strand Street &, 24A... -33.920610  18.421170   
2      199 Voortrekker Rd, Maitland, Cape Town, 7405 -33.922920  18.485990   
3  Cnr Koeberg &, Bosmansdam Rd, Milnerton, Cape ... -33.877860  18.499540   
4   Kloof St, Gardens, Cape Town, 800,  021 422 1371 -33.931932  18.408858   

                     geometry  
0  POINT (18.50640 -33.93582)  
1  POINT (18.42117 -33.92061)  
2  POINT (18.48599 -33.92292)  
3  POINT (18.49954 -33.87786)  
4  POINT (18.40886 -33.93193)

#Here the graph we create a grap map 

The documentation of all the parameters available for creating graphs can be found here:

https://osmnx.readthedocs.io/en/stable/osmnx.html#module-osmnx.graph  
    

In [15]:
place = "Cape Town, South Africa"
# 2. Transportation mode
mode = "drive"
# 3. Create network graph from place and mode
G = ox.graph_from_address(place, dist=1500, simplify=True, network_type=mode)


graph_map = ox.plot_graph_folium(G, popup_attribute='name', edge_width=2)
graph_map

In [16]:
gdf_nodes = ox.graph_to_gdfs(G, edges=False)
gdf_nodes.head()

y          x  street_count  ref            highway  \
osmid                                                                  
21321047 -33.918791  18.418944             4  NaN                NaN   
21321059 -33.925560  18.429974             3  NaN                NaN   
25450460 -33.917394  18.430866             3  NaN                NaN   
25450504 -33.917110  18.431618             3  NaN                NaN   
25499449 -33.926112  18.433197             3   1B  motorway_junction   

                            geometry  
osmid                                 
21321047  POINT (18.41894 -33.91879)  
21321059  POINT (18.42997 -33.92556)  
25450460  POINT (18.43087 -33.91739)  
25450504  POINT (18.43162 -33.91711)  
25499449  POINT (18.43320 -33.92611)

In [16]:
edges = ox.graph_to_gdfs(G, nodes=False, edges=True)
edges.head()

osmid  \
u        v        key                                                      
21321047 25580664 0                                            696724213   
         25897046 0                               [742323293, 740406391]   
21321059 25580881 0                               [424981973, 424981974]   
25450504 25499450 0    [405901606, 423448617, 61131981, 740432976, 55...   
25499449 25499459 0                         [4256019, 4256018, 61131979]   

                       oneway   lanes   ref                      name  \
u        v        key                                                   
21321047 25580664 0      True       3  R102             Strand Street   
         25897046 0      True       3   M62       Buitengracht Street   
21321059 25580881 0      True       4  R102             Strand Street   
25450504 25499450 0      True       2    N2  Nelson Mandela Boulevard   
25499449 25499459 0      True  [2, 4]   NaN                       NaN   

                             highway maxspeed reversed    length  \
u        v        key                                              
21321047 25580664 0          primary       60    False    16.114   
         25897046 0          primary       60    False    71.577   
21321059 25580881 0          primary       60    False   357.556   
25450504 25499450 0         motorway       80    False  1301.928   
25499449 25499459 0    motorway_link       80    False   347.609   

                                                                geometry  \
u        v        key                                                      
21321047 25580664 0    LINESTRING (18.41894 -33.91879, 18.41907 -33.9...   
         25897046 0    LINESTRING (18.41894 -33.91879, 18.41902 -33.9...   
21321059 25580881 0    LINESTRING (18.42997 -33.92556, 18.42843 -33.9...   
25450504 25499450 0    LINESTRING (18.43162 -33.91711, 18.43221 -33.9...   
25499449 25499459 0    LINESTRING (18.43320 -33.92611, 18.43316 -33.9...   

                      bridge width access junction tunnel  
u        v        key                                      
21321047 25580664 0      NaN   NaN    NaN      NaN    NaN  
         25897046 0      NaN   NaN    NaN      NaN    NaN  
21321059 25580881 0      NaN   NaN    NaN      NaN    NaN  
25450504 25499450 0      yes   NaN    NaN      NaN    NaN  
25499449 25499459 0      yes   NaN    NaN      NaN    NaN

In [18]:
gdf_nodes['ref'].unique()

array([nan, '1B', '1', '1A'], dtype=object)

In [19]:
gdf_nodes['highway'].unique()

array([nan, 'motorway_junction', 'traffic_signals', 'stop',
       'turning_circle', 'crossing'], dtype=object)

In [20]:
center_node = ox.distance.nearest_nodes(G, -33.9152209,18.3758852)

In [21]:
trip_times = [5, 15, 25, 40, 60]

In [22]:
travel_speed = 4.5

In [23]:
meters_per_minute = travel_speed * 1000 / 60

In [24]:
for u, v, k, data in G.edges(data=True, keys=True):
       data["time"] = data["length"] / meters_per_minute
        

In [25]:
 polys = []
for trip_time in trip_times:
    subgraph = nx.ego_graph(G, center_node, radius=trip_time, distance="time")
    node_points = [Point(data["x"], data["y"]) for node, data in subgraph.nodes(data=True)]
    polys.append(gpd.GeoSeries(node_points).unary_union.convex_hull)


In [25]:
def get_isochrone(
    lon, lat, drive_times=[5,10], speed=60, name=None, point_index=None
):
    loc = (lat, lon)
    G = ox.graph_from_point(loc, simplify=True, network_type="drive")
    gdf_nodes = ox.graph_to_gdfs(G, edges=False)
    center_node = ox.distance.nearest_nodes(G, lon, lat)

    meters_per_minute = speed * 1000 / 60  # km per hour to m per minute
    for u, v, k, data in G.edges(data=True, keys=True):
        data["time"] = data["length"] / meters_per_minute
    polys = []
    for drive_time in drive_times:
        subgraph = nx.ego_graph(G, center_node, radius=drive_time, distance="time")
        node_points = [
            Point(data["x"], data["y"]) for node, data in subgraph.nodes(data=True)
        ]
        polys.append(gpd.GeoSeries(node_points).unary_union.convex_hull)
    info = {}
    if name:
        info["name"] = [name for t in drive_times]
    if point_index:
        info["point_index"] = [point_index for t in drive_times]
    return {**{"geometry": polys, "time": drive_times}, **info}


In [26]:
df_polys = df.apply(lambda x: get_isochrone(x.long, x.latt), axis=1)

In [28]:
df_polys.head(11)

0     {'geometry': [POLYGON ((18.5091627 -33.9447882...
1     {'geometry': [POLYGON ((18.4256371 -33.9295957...
2     {'geometry': [POLYGON ((18.4869229 -33.9313973...
3     {'geometry': [POLYGON ((18.4926796 -33.8867358...
4     {'geometry': [POLYGON ((18.4151968 -33.940835,...
5     {'geometry': [POLYGON ((18.4703012 -33.969329,...
6     {'geometry': [POLYGON ((18.5065453 -33.8945856...
7     {'geometry': [POLYGON ((18.5472071 -33.9689518...
8     {'geometry': [POLYGON ((18.4612304 -33.9904371...
9     {'geometry': [POLYGON ((18.3822657 -33.9247538...
10    {'geometry': [POLYGON ((18.419101 -33.9341628,...
dtype: object

In [45]:
DT = [5,10] #drive times can be list of times 
stores = df_geo.head()

isochrones = pd.concat(
    [
        gpd.GeoDataFrame(
            get_isochrone(
                r["geometry"].x,
                r["geometry"].y,
                name=r["Store"],
                point_index=i+1,
                drive_times=DT
            ),
            crs=df_geo.crs,
        )
        for i, r in stores.iterrows()
    ]
)

In [46]:
isochrones.head()

geometry  time  \
0  POLYGON ((18.50916 -33.94479, 18.49559 -33.944...     5   
1  POLYGON ((18.50916 -33.94479, 18.49559 -33.944...    10   
0  POLYGON ((18.42564 -33.92960, 18.41227 -33.929...     5   
1  POLYGON ((18.42564 -33.92960, 18.41227 -33.929...    10   
0  POLYGON ((18.48692 -33.93140, 18.48085 -33.930...     5   

                                                name  point_index  
0  Howard Centre, Forest Dr Service Rd, Pinelands...            1  
1  Howard Centre, Forest Dr Service Rd, Pinelands...            1  
0  Cape Town City Centre Cnr Strand Street &, 24A...            2  
1  Cape Town City Centre Cnr Strand Street &, 24A...            2  
0      199 Voortrekker Rd, Maitland, Cape Town, 7405            3

In [44]:
folium.GeoJson(isochrones.to_json(), style_function=lambda x:{'fillColor': 'red'}).add_to(m)
m

In [24]:
isochrones.to_file('polygons.geojson')

In [ ]:
df_new_polys = df.apply(lambda x: get_isochrone(x.long, x.latt), axis=1)
df_new_polys.crs = 'epsg:4326'

In [ ]:
type(df_new_polys)

In [ ]:
df_new_polys.rename('geo', inplace=True)

In [ ]:
G = ox.graph_from_point(df_new_polys, simplify=True, network_type='walk')


In [ ]:
print(df_new_polys.dtypes)
print(type(df_new_polys))

In [ ]:
for _, r in df.iterrows():
    sim_geo = df_new_polys.GeoSeries(r['geometry'])
    sim_geo.set_crs(epsg="original_epsg_of_shapefile", inplace=True)
    sim_geo = sim_geo.to_crs("EPSG:4326") # convert to epsg 4326 to display on map and not 3857
#     sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001) #req only if you have multipolygon
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {'fillColor': 'orange'})
#     folium.Popup(r['ID']).add_to(geo_j)
    geo_j.add_to(map)

In [ ]:
df_new_polys = pd.DataFrame(df_new_polys, columns = ['geo'])

In [ ]:
for i in range(0,len(df_new_polys)-1):
    df =  df_new_polys.loc[:i,:]
    print(df.info())

In [ ]:
df_new_polys.head()

In [ ]:
df_new_polys.dtypes

In [ ]:
#gpdf_new_polys.to_crs(epsg=4326)

In [ ]:
type(df_new_polys)

In [ ]:
#poly_df_3 = df_new_polyss[df_new_polyss.geometry.type == 'Polygon']
#poly_df_3

In [ ]:
#df_new_polys = pd.to_numeric(df_new_polys['geometry'])

In [ ]:
df_json = gpdf_new_polys.to_json
df_json

In [ ]:
for _, r in df.iterrows():
    sim_geo = df_new_polys.GeoSeries(r['geometry'])
    sim_geo.set_crs(epsg="original_epsg_of_shapefile", inplace=True)
    sim_geo = sim_geo.to_crs("EPSG:4326") # convert to epsg 4326 to display on map and not 3857
#     sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001) #req only if you have multipolygon
    geo_j = sim_geo.to_json()
    geo_j = folium.GeoJson(data=geo_j, style_function=lambda x: {'fillColor': 'orange'})
#     folium.Popup(r['ID']).add_to(geo_j)
    geo_j.add_to(map)

In [ ]:
folium.GeoJson(df_json, style_function=lambda x:{'fillColor': 'red'}).add_to(m)
m

In [ ]:
from shapely import wkt
import pandas as pd

In [ ]:
df_new_polys['geom'] = df_new_polys[''].apply(wkt.loads)

In [ ]:
print(df_new_polys.columns)

In [ ]:
df_new_polys['geometry'] = df_new_polys.columns.astype('geometry')
df_new_polys['geometry'].dtype

In [ ]:
def get_isochrone(lon, lat, walk_time=10, speed=4.5):
    loc = (lat, lon)
    G = ox.graph_from_point(loc, simplify=True, network_type='walk')
    G = ox.project_graph(G, to_crs="4483") # Use this line if the coordinates sistem returned from polys is changed from the original (check which crs you are using)
    gdf_nodes = ox.graph_to_gdfs(G, edges=False)
    x, y = gdf_nodes['geometry'].unary_union.centroid.xy
    center_node = ox.nearest_nodes(G, Y = y[0], X= x[0])
    walking_meters = walk_time * speed * 1000 / 60 #km per hour to m per minute times the minutes to walk
    subgraph = nx.ego_graph(G, center_node, radius=walking_meters, distance='length')
    node_points = [Point(data['x'], data['y']) for node, data in subgraph.nodes(data=True)]
    polys = gpd.GeoSeries(node_points).unary_union.convex_hull
    return {polys}